In [1]:
import pandas as pd
import plotly.graph_objs as go

In [2]:
df_circuits = pd.read_csv('./data/circuits.csv', header = 0)
df_drivers = pd.read_csv('./data/drivers.csv',header = 0)
df_races = pd.read_csv('./data/races.csv',header = 0, delimiter = ';')
df_results = pd.read_csv('./data/results.csv',header = 0)
#df_circuits = pd.read_csv('./data/circuits.csv')
df_laps = pd.read_csv('./data/lap_times.csv',header = 0)

df_races.set_index('raceId', inplace=True)
df_results.set_index('resultId', inplace=True)
df_drivers.set_index('driverId', inplace=True)

In [3]:
df_final = pd.read_excel('./data/circuits_drivers_races_constructors_results.xlsx')

In [4]:
circuit_name = 'Buddh International Circuit'

### Circuit Information

In [5]:
df_final_circuit =  df_final.loc[(df_final['circuits.name'] == str(circuit_name))]


In [6]:
list(range(1950,2023,5))

[1950,
 1955,
 1960,
 1965,
 1970,
 1975,
 1980,
 1985,
 1990,
 1995,
 2000,
 2005,
 2010,
 2015,
 2020]

In [7]:
df_final_circuit.columns

Index(['resultId', 'raceId', 'driverId', 'positionText', 'positionOrder',
       'races.raceId', 'races.year', 'races.circuitId', 'races.name',
       'drivers.forename', 'drivers.surname', 'drivers.nationality',
       'circuits.name', 'circuits.location', 'circuits.country',
       'circuits.lat', 'circuits.lng', 'constructors.constructorRef',
       'constructors.name', 'constructors.nationality', 'constructorId'],
      dtype='object')

In [8]:
df_final_circuit['drivers.fullname'] = df_final_circuit[['drivers.forename','drivers.surname']].apply(lambda x: ' '.join(x), axis=1)

C:\Users\Admin\AppData\Local\Temp/ipykernel_644/3853478060.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_final_circuit['drivers.fullname'] = df_final_circuit[['drivers.forename','drivers.surname']].apply(lambda x: ' '.join(x), axis=1)


In [9]:
city = df_final_circuit['circuits.location'].unique()[0]
country = df_final_circuit['circuits.country'].unique()[0]

In [10]:
best_driver = df_final_circuit[(df_final_circuit['circuits.name'] == circuit_name) & (df_final_circuit['positionText'] == 1)].groupby('drivers.fullname')['drivers.fullname'].count().sort_values(ascending = False).index.tolist()[0]

In [11]:
best_constructor = df_final_circuit[(df_final_circuit['circuits.name'] == circuit_name) & (df_final_circuit['positionText'] == 1)].groupby('constructors.name')['constructors.name'].count().sort_values(ascending = False).index.tolist()[0]

In [12]:
number_ret = len(df_final_circuit[df_final_circuit['positionText'] == 'R'])

In [13]:
df_final_circuit[(df_final_circuit['circuits.name'] == circuit_name) & (df_final_circuit['positionText'] == 1)].groupby(['races.year','drivers.fullname'])['drivers.fullname'].count().sort_values(ascending = True)

races.year  drivers.fullname
2011        Sebastian Vettel    1
2012        Sebastian Vettel    1
2013        Sebastian Vettel    1
Name: drivers.fullname, dtype: int64

In [14]:
# erro possivel aqui --- averiguar
recent_driver_win, year_win = df_final_circuit[(df_final_circuit['circuits.name'] == circuit_name) & (df_final_circuit['positionText'] == 1)].groupby(['drivers.fullname','races.year'])['drivers.fullname'].count().sort_values(ascending = False).index.tolist()[0]

In [15]:
recent_driver_win, year_win

('Sebastian Vettel', 2011)

### No race result vs finished race

In [16]:
ret_list = ['R', 'F', 'W', 'N', 'D','E']

In [17]:
dvsc_value = 'Constructors'

In [18]:
if dvsc_value == 'Drivers': 
        filter_dc = 'drivers.fullname'
else: filter_dc = 'constructors.name'

In [19]:
plot_percentages = pd.DataFrame(columns=[filter_dc,'dnf','nraces'])

In [20]:
# procurar caterham

In [21]:
dc_n_list = df_final_circuit[filter_dc].unique().tolist()
race_n_list = []
dnf_n_list = []

for dc in dc_n_list: 
    race_count = 0
    dnf_count = 0
    for j, dc_name in enumerate(df_final_circuit[filter_dc]):
        if dc == dc_name: 
            if df_final_circuit['positionText'].iloc[j] in ret_list:
                dnf_count+=1
            race_count+=1

    dnf_n_list.append(dnf_count)
    race_n_list.append(race_count)



In [22]:
plot_percentages[filter_dc] = dc_n_list
plot_percentages.dnf = dnf_n_list
plot_percentages.nraces = race_n_list

In [23]:
plot_percentages

constructors.name  dnf  nraces
0             Virgin    1       2
1           Williams    1       6
2           Lotus F1    0       4
3            McLaren    0       6
4         Toro Rosso    1       6
5            Ferrari    1       6
6            Renault    0       2
7                HRT    1       4
8           Caterham    2       4
9           Marussia    0       4
10             Lotus    0       2
11       Force India    0       6
12          Mercedes    0       6
13            Sauber    2       6
14          Red Bull    1       6

In [24]:
# NÃO ESQUECER QUE PODE HAVER CIRCUITOS SEM DNFS

In [25]:
# não esta a dar ainda 

In [26]:
plot_percentages['dnf_percentage'] = plot_percentages['dnf'] / plot_percentages['nraces']
plot_percentages['nraces_percentage'] = 1-plot_percentages['dnf_percentage']

In [27]:
plot_percentages[plot_percentages[filter_dc]=='Virgin']

constructors.name  dnf  nraces  dnf_percentage  nraces_percentage
0            Virgin    1       2             0.5                0.5

In [28]:
plot_percentages

constructors.name  dnf  nraces  dnf_percentage  nraces_percentage
0             Virgin    1       2        0.500000           0.500000
1           Williams    1       6        0.166667           0.833333
2           Lotus F1    0       4        0.000000           1.000000
3            McLaren    0       6        0.000000           1.000000
4         Toro Rosso    1       6        0.166667           0.833333
5            Ferrari    1       6        0.166667           0.833333
6            Renault    0       2        0.000000           1.000000
7                HRT    1       4        0.250000           0.750000
8           Caterham    2       4        0.500000           0.500000
9           Marussia    0       4        0.000000           1.000000
10             Lotus    0       2        0.000000           1.000000
11       Force India    0       6        0.000000           1.000000
12          Mercedes    0       6        0.000000           1.000000
13            Sauber    2       6        0.333333           0.666667
14          Red Bull    1       6        0.166667           0.833333

In [29]:
plot_percentages[(plot_percentages.nraces != 1) & (plot_percentages.nraces != 0)]

constructors.name  dnf  nraces  dnf_percentage  nraces_percentage
0             Virgin    1       2        0.500000           0.500000
1           Williams    1       6        0.166667           0.833333
2           Lotus F1    0       4        0.000000           1.000000
3            McLaren    0       6        0.000000           1.000000
4         Toro Rosso    1       6        0.166667           0.833333
5            Ferrari    1       6        0.166667           0.833333
6            Renault    0       2        0.000000           1.000000
7                HRT    1       4        0.250000           0.750000
8           Caterham    2       4        0.500000           0.500000
9           Marussia    0       4        0.000000           1.000000
10             Lotus    0       2        0.000000           1.000000
11       Force India    0       6        0.000000           1.000000
12          Mercedes    0       6        0.000000           1.000000
13            Sauber    2       6        0.333333           0.666667
14          Red Bull    1       6        0.166667           0.833333

In [30]:
drivers_client = ['Virgin', 'Red Bull', 'Ferrari']

In [31]:
pplot_percentages = plot_percentages.loc[plot_percentages[filter_dc].isin(drivers_client)]

In [32]:
fig = go.Figure()
fig.add_trace(go.Bar(
    y=pplot_percentages[filter_dc],
    x=pplot_percentages['dnf_percentage'],
    name='DNF',
    orientation='h',   
    marker=dict(
        color='rgba(153, 0, 0, 0.6.0)',
        line=dict(color='rgba(153, 0, 0, 1.0)', width=1)
    )
))
fig.add_trace(go.Bar(
    y=pplot_percentages[filter_dc],
    x=pplot_percentages['nraces_percentage'],
    name='No DNF',
    orientation='h',
    marker=dict(
        color='rgba(69, 69, 69, 0.6)',
        line=dict(color='rgba(0, 0, 0, 1)', width=1)
    )
))

fig.update_layout(barmode='stack')
fig.show()

In [33]:
# plot de dnfs por equipa
plot_df_ret = df_final_circuit[(df_final_circuit['circuits.name'] == circuit_name) & (df_final_circuit['positionText'].isin(ret_list))].groupby(filter_dc).count()
plot_df_ret.reset_index(inplace=True)
bad_list = plot_df_ret[filter_dc].unique()
# plot de corridas acabadas por equipa 
plot_df_fin = df_final_circuit[(df_final_circuit['circuits.name'] == circuit_name) & (df_final_circuit[filter_dc].isin(bad_list))].groupby(filter_dc).count()
plot_df_fin.reset_index(inplace=True)

### Lap times

In [146]:
races_list = df_final_circuit['raceId'].unique()

In [147]:
date_list = df_final_circuit['races.year'].unique()

In [148]:
df_laps_circuit = df_laps.loc[(df_laps['raceId'].isin(races_list))]

In [149]:
df_laps_circuit

raceId  driverId  lap  position      time  milliseconds
20075     857        20    1         1  1:34.881         94881
20076     857        20    2         1  1:33.738         93738
20077     857        20    3         1  1:32.770         92770
20078     857        20    4         1  1:32.377         92377
20079     857        20    5         1  1:32.703         92703
...       ...       ...  ...       ...       ...           ...
68369     896       819   32        21  1:32.907         92907
68370     896       819   33        21  1:35.064         95064
68371     896       819   34        21  1:33.759         93759
68372     896       819   35        21  1:39.286         99286
68373     896       823    1        22  2:42.390        162390

[3755 rows x 6 columns]

In [150]:
df_laps_drivers = df_laps_circuit.groupby(['raceId','driverId'])['time'].min()

In [151]:
df_laps_drivers.reset_index()

raceId  driverId      time
0      857         1  1:28.721
1      857         3  1:28.600
2      857         4  1:27.953
3      857         5  1:30.294
4      857        10  1:56.549
..     ...       ...       ...
64     896       820  1:30.335
65     896       821  1:28.682
66     896       822  1:28.928
67     896       823  2:42.390
68     896       824  1:30.171

[69 rows x 3 columns]

In [152]:
df_fastest_lap = df_laps_drivers.groupby('raceId').min().reset_index()

In [153]:
df_fastest_lap['year'] = date_list

In [154]:
df_fastest_lap

raceId      time  year
0     857  1:27.249  2011
1     876  1:28.203  2012
2     896  1:27.679  2013

In [155]:
fig = go.Figure(data=go.Scatter(y=df_fastest_lap.time, x=df_fastest_lap.year))
fig.show()

#### Driver Plot

In [171]:
races_list = df_final_circuit['raceId'].unique()
date_list = df_final_circuit['races.year'].unique()

In [172]:
df_laps_circuit = df_laps.loc[(df_laps['raceId'].isin(races_list))]

In [173]:
df_laps_circuit_test = df_laps_circuit.copy()

In [174]:
df_laps_circuit_test

raceId  driverId  lap  position      time  milliseconds
20075     857        20    1         1  1:34.881         94881
20076     857        20    2         1  1:33.738         93738
20077     857        20    3         1  1:32.770         92770
20078     857        20    4         1  1:32.377         92377
20079     857        20    5         1  1:32.703         92703
...       ...       ...  ...       ...       ...           ...
68369     896       819   32        21  1:32.907         92907
68370     896       819   33        21  1:35.064         95064
68371     896       819   34        21  1:33.759         93759
68372     896       819   35        21  1:39.286         99286
68373     896       823    1        22  2:42.390        162390

[3755 rows x 6 columns]

In [169]:
df_laps_circuit_test['laprace'] = df_laps_circuit['lap'] + ',' + df_laps_circuit['raceId']

In [170]:
df_laps_circuit_test['laprace']

20075    20075     1\n20076     2\n20077     3\n20078  ...
20076    20075     1\n20076     2\n20077     3\n20078  ...
20077    20075     1\n20076     2\n20077     3\n20078  ...
20078    20075     1\n20076     2\n20077     3\n20078  ...
20079    20075     1\n20076     2\n20077     3\n20078  ...
                               ...                        
68369    20075     1\n20076     2\n20077     3\n20078  ...
68370    20075     1\n20076     2\n20077     3\n20078  ...
68371    20075     1\n20076     2\n20077     3\n20078  ...
68372    20075     1\n20076     2\n20077     3\n20078  ...
68373    20075     1\n20076     2\n20077     3\n20078  ...
Name: laprace, Length: 3755, dtype: object

In [142]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_laps_circuit['lap/race'], y=df_laps_circuit[df_laps_circuit.driverId == 20].milliseconds,
                    mode='lines',
                    name='20'))
fig.add_trace(go.Scatter(x=df_laps_circuit['lap/race'], y=df_laps_circuit[df_laps_circuit.driverId == 819].milliseconds,
                    mode='lines',
                    name='19'))
fig.add_trace(go.Scatter(x=df_laps_circuit['lap/race'], y=df_laps_circuit[df_laps_circuit.driverId == 18].milliseconds,
                    mode='lines', name='18'))

fig.show()

In [104]:
df_laps_driver_spec = df_laps_circuit.groupby(['raceId','driverId'])

In [105]:
df_laps_driver_spec

In [99]:
df_laps_driver_spec[df_laps_driver_spec.driverId == 5]

raceId  driverId  milliseconds
3      857         5         90294
26     876         5         90786

### Box Plot 

In [ ]:
df_final[(df_final['circuits.name'] == circuit_name) & (df_final['positionText'] == 1)].groupby('drivers.surname')['drivers.surname'].count().sort_values(ascending = False).index.tolist()

['Hamilton',
 'Vettel',
 'Alonso',
 'Massa',
 'Button',
 'Leclerc',
 'Pérez',
 'Rosberg',
 'Schumacher']

In [ ]:
def get_circuit_id(circuit_name):
    for index,circuit in enumerate(df_circuits): 
        if df_circuits['name'][index] == circuit_name:
            id_circuit = df_circuits['circuitId'][index]

    return id_circuit

In [ ]:
def get_driver_name(driver_id):
    for driver in df_drivers.index: 
        if driver == driver_id:
            driver_name = df_drivers['forename'][driver] + ' '+ df_drivers['surname'][driver]

    return driver_name

In [ ]:
def best_pilot_circuit(circuit): 
    # get the races in the circuit 
    race_list = df_races[df_races.circuitId == get_circuit_id(circuit_name)].index.tolist()
    # get the winning drivers from that circuit
    drivers_list = df_results[(df_results['raceId'].isin(race_list)) & (df_results['positionText'] == '1')].groupby('driverId')['driverId'].count().sort_values(ascending = False).index.tolist()
    # get the number of wins by each driver 
    winning_list = df_results[(df_results['raceId'].isin(race_list)) & (df_results['positionText'] == '1')].groupby('driverId')['driverId'].count().sort_values(ascending = False).tolist()
    
    # convert drivers id into names
    drivers_names = []
    for driver_id in drivers_list: 
        drivers_names.append(get_driver_name(driver_id))

    d = {'Drivers':drivers_names,'Wins':winning_list}
    df_wins = pd.DataFrame(d)

    fig = px.histogram(df, x="day", category_orders=dict(day=["Thur", "Fri", "Sat", "Sun"]))
    fig.show()
    

### Pie Chart 

In [100]:
df_final.columns

Index(['resultId', 'raceId', 'driverId', 'positionText', 'positionOrder',
       'races.raceId', 'races.year', 'races.circuitId', 'races.name',
       'drivers.forename', 'drivers.surname', 'drivers.nationality',
       'circuits.name', 'circuits.location', 'circuits.country',
       'circuits.lat', 'circuits.lng', 'constructors.constructorRef',
       'constructors.name', 'constructors.nationality', 'constructorId'],
      dtype='object')

In [101]:
const_wins = df_final[(df_final['circuits.name'] == circuit_name) & (df_final['positionText'] == 1)].groupby('constructors.name')['constructors.name'].count().sort_values(ascending = False).tolist()

In [102]:
const_names = df_final[(df_final['circuits.name'] == circuit_name) & (df_final['positionText'] == 1)].groupby('constructors.name')['constructors.name'].count().sort_values(ascending = False).index.tolist()

In [103]:
import plotly.express as px
# This dataframe has 244 lines, but 4 distinct values for `day`

fig = px.pie(values=const_wins, names=const_names,color_discrete_sequence=px.colors.sequential.RdBu)
fig.show()

In [104]:
df_final[(df_final['circuits.name'] == circuit_name) & (df_final['positionText'] == 1)].groupby('constructors.name')['constructors.name'].count().sort_values(ascending = False).tolist()

[7, 6, 2, 2, 1, 1]

In [105]:
df = df_final[(df_final['circuits.name'] == circuit_name) & (df_final['positionText'] == 1)].groupby('constructors.name')['drivers.surname'].count()

In [106]:
contructors =df_final[(df_final['circuits.name'] == circuit_name) & (df_final['positionText'] == 1)].groupby(['constructors.name', 'drivers.surname']).agg({'resultId': 'nunique'})

In [107]:
only_winners = df_final[(df_final['circuits.name'] == circuit_name) & (df_final['positionText'] == 1)]

In [108]:
only_winners

resultId  raceId  driverId positionText  positionOrder  races.raceId  \
5519      24926    1046       815            1              1          1046   
10907      7614       4        18            1              1             4   
16227        45      20        13            1              1            20   
16233       413      38        13            1              1            38   
16358     20323     337         4            1              1           337   
16373     23419     971        20            1              1           971   
16378     23802     990        20            1              1           990   
16386     25406    1074       844            1              1          1074   
16397      1555      92        30            1              1            92   
17826       743      53         4            1              1            53   
17844      1179      73         4            1              1            73   
21127     22174     902         1            1              1           902   
21139     22596     929         1            1              1           929   
21177     24223    1011         1            1              1          1011   
21198     24906    1045         1            1              1          1045   
21199     24966    1052         1            1              1          1052   
22432     21304     863        20            1              1           863   
22451     21778     883        20            1              1           883   
22903     22939     949         3            1              1           949   

       races.year  races.circuitId          races.name drivers.forename  ...  \
5519         2020                3   Sakhir Grand Prix           Sergio  ...   
10907        2009                3  Bahrain Grand Prix           Jenson  ...   
16227        2008                3  Bahrain Grand Prix           Felipe  ...   
16233        2007                3  Bahrain Grand Prix           Felipe  ...   
16358        2010                3  Bahrain Grand Prix         Fernando  ...   
16373        2017                3  Bahrain Grand Prix        Sebastian  ...   
16378        2018                3  Bahrain Grand Prix        Sebastian  ...   
16386        2022                3  Bahrain Grand Prix          Charles  ...   
16397        2004                3  Bahrain Grand Prix          Michael  ...   
17826        2006                3  Bahrain Grand Prix         Fernando  ...   
17844        2005                3  Bahrain Grand Prix         Fernando  ...   
21127        2014                3  Bahrain Grand Prix            Lewis  ...   
21139        2015                3  Bahrain Grand Prix            Lewis  ...   
21177        2019                3  Bahrain Grand Prix            Lewis  ...   
21198        2020                3  Bahrain Grand Prix            Lewis  ...   
21199        2021                3  Bahrain Grand Prix            Lewis  ...   
22432        2012                3  Bahrain Grand Prix        Sebastian  ...   
22451        2013                3  Bahrain Grand Prix        Sebastian  ...   
22903        2016                3  Bahrain Grand Prix             Nico  ...   

      drivers.nationality                  circuits.name circuits.location  \
5519              Mexican  Bahrain International Circuit            Sakhir   
10907             British  Bahrain International Circuit            Sakhir   
16227           Brazilian  Bahrain International Circuit            Sakhir   
16233           Brazilian  Bahrain International Circuit            Sakhir   
16358             Spanish  Bahrain International Circuit            Sakhir   
16373              German  Bahrain International Circuit            Sakhir   
16378              German  Bahrain International Circuit            Sakhir   
16386          Monegasque  Bahrain International Circuit            Sakhir   
16397              German  Bahrain International Circuit            Sakhir   
17826             Spanish  Bahrain Internatio

In [109]:
contructors.reset_index(inplace = True)

In [110]:
contructors

constructors.name drivers.surname  resultId
0              Brawn          Button         1
1            Ferrari          Alonso         1
2            Ferrari         Leclerc         1
3            Ferrari           Massa         2
4            Ferrari      Schumacher         1
5            Ferrari          Vettel         2
6           Mercedes        Hamilton         5
7           Mercedes         Rosberg         1
8       Racing Point           Pérez         1
9           Red Bull          Vettel         2
10           Renault          Alonso         2

In [207]:
import plotly.express as px
df = px.data.tips()
fig = px.sunburst(contructors, path=['constructors.name', 'drivers.surname'], values='resultId',color_discrete_sequence=px.colors.sequential.RdBu)
fig.show()